In [27]:
import pandas as pd
import numpy as np
from sklearn.model_selection import train_test_split
from sklearn.decomposition import PCA
from sklearn.neighbors import KNeighborsClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.svm import SVC
from sklearn.metrics import balanced_accuracy_score
import matplotlib.pyplot as plt
import json
from sklearn.preprocessing import StandardScaler

In [4]:
#matchStats_df= pd.read_csv('../datafilev2/datafile/season17-18/season_match_stats.csv')
#seasonStats_df = pd.read_csv('../datafilev2/datafile/season17-18/season_stats.csv')
with open('../datafilev2/datafile/season17-18/season_stats.json', encoding='UTF-8') as f:
    #data = ''.join(f.readlines())
    #data_dict = json.loads(data)
    d = json.load(f)
    
#szn_1718 = pd.read_json('../datafilev2/datafile/season17-18/season_stats.json', encoding='UTF-8')

#season_1718 = json.load(open('../datafilev2/datafile/season17-18/season_stats.json', encoding='UTF-8'))


In [7]:
#data_dict
d

{'1190174': {'13': {'team_details': {'team_id': '13',
    'team_name': 'Arsenal',
    'team_rating': '7.30714285714286',
    'date': '11/08/2017'},
   'aggregate_stats': {'fk_foul_lost': '9',
    'won_contest': '16',
    'possession_percentage': '70',
    'total_throws': '21',
    'att_miss_high_left': '1',
    'blocked_scoring_att': '8',
    'total_scoring_att': '27',
    'att_sv_low_left': '1',
    'total_tackle': '23',
    'att_miss_high_right': '2',
    'aerial_won': '18',
    'att_miss_right': '3',
    'att_sv_low_centre': '2',
    'att_miss_high': '1',
    'aerial_lost': '18',
    'att_sv_low_right': '2',
    'total_pass': '632',
    'won_corners': '9',
    'shot_off_target': '9',
    'ontarget_scoring_att': '10',
    'goals': '4',
    'att_miss_left': '2',
    'att_goal_low_left': '2',
    'total_offside': '5',
    'att_sv_high_centre': '1',
    'accurate_pass': '538',
    'att_goal_high_left': '1',
    'att_goal_low_centre': '1'},
   'Player_stats': {'Petr Cech': {'player_detai

In [8]:
#I am going to try code I found in the same page that the dataset was available.
# It shows how this one guy read this dataset into a dataframe, further testing is required (4/21 9:43pm).... 

# create a dictionary containing lists
team_table = {'match_id':[]} ## I (well, actually jordan) sort of did this up above with data_dict

# read through original data
for match_id, match_content in d.items():
    for match_stats in match_content.values():
        team_table['match_id'].append(match_id)
        
        for team_details_label,team_details in match_stats['team_details'].items():
            if team_details_label not in team_table.keys():
                team_table[team_details_label] = []
            team_table[team_details_label].append(team_details)
        
        for team_stats_label,team_stats in match_stats['aggregate_stats'].items():
            if team_stats_label not in team_table.keys():
                team_table[team_stats_label] = []

In [9]:
#right here im just testing shit from above, making sure we getting data correctly listed
match_stats['aggregate_stats'] 

{'att_goal_low_right': '1',
 'won_contest': '5',
 'possession_percentage': '47.5',
 'total_throws': '22',
 'att_miss_high_left': '1',
 'blocked_scoring_att': '5',
 'total_scoring_att': '16',
 'total_tackle': '17',
 'att_miss_high_right': '2',
 'aerial_won': '16',
 'att_miss_right': '1',
 'att_sv_high_left': '1',
 'att_sv_low_centre': '2',
 'aerial_lost': '24',
 'total_pass': '406',
 'won_corners': '6',
 'shot_off_target': '6',
 'ontarget_scoring_att': '5',
 'goals': '2',
 'att_miss_left': '2',
 'fk_foul_lost': '16',
 'att_goal_low_left': '1',
 'total_offside': '3',
 'accurate_pass': '324'}

In [11]:
#this, again, is from the source mentioned above....

# so far I've created a dictionary containing all the match&team information,
# but no statistic is filled in due to that not all teams have all the data in every matches,
# now I have to deal with missing data:
# filling all statistics with np.nan
for k,v in team_table.items():
    if len(v) == 0:
        team_table[k] = [np.nan] * len(team_table['match_id'])

# indexing by match ID and team ID, if they both matches, fill in the real data
for pos in range(len(team_table['match_id'])):
    for match_id,match_content in d.items():
        for team_id, match_stats in match_content.items():
            for team_stats_label,team_stats in match_stats['aggregate_stats'].items():
                if (team_table['match_id'][pos] == match_id) & (team_table['team_id'][pos] == team_id):
                    team_table[team_stats_label][pos] = team_stats

df = pd.DataFrame(team_table)
df
team_match_data = df.to_csv()
#df.to_csv('team_match_data1718.csv')

In [14]:
#mainly testing to make sure team_table stuff is converted to csv
pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)
pd.set_option('display.width', None)
pd.set_option('display.max_colwidth', -1)
df
#df.to_csv('team_match_data1718_1.csv')

<ipython-input-14-65c75b292717>:5: FutureWarning: Passing a negative integer is deprecated in version 1.0 and will not be supported in future version. Instead, use None to not limit the column width.
  pd.set_option('display.max_colwidth', -1)


In [ ]:
df = df.fillna(0)
#df = df.drop('Unnamed: 0', axis=1)

In [29]:
df = pd.read_csv('team_match_data.csv')
df

Unnamed: 0  match_id  team_id             team_name  team_rating  \
0    0           1190418   166      Huddersfield          6.140000      
1    1           1190418   26       Liverpool             7.222857      
2    2           1190424   211      Brighton              7.153846      
3    3           1190424   183      Bournemouth           6.902857      
4    4           1190342   15       Chelsea               6.771429      
5    5           1190342   14       Leicester             6.955000      
6    6           1190356   26       Liverpool             7.844286      
7    7           1190356   259      Swansea               5.831429      
8    8           1190430   15       Chelsea               6.489286      
9    9           1190430   183      Bournemouth           7.367143      
10   10          1190381   15       Chelsea               7.011429      
11   11          1190381   162      Crystal Palace        6.748571      
12   12          1190395   23       Newcastle United      7.194286      
13   13          1190395   32       Manchester United     6.575000      
14   14          1190183   175      West Bromwich Albion  7.028571      
15   15          1190183   183      Bournemouth           6.503571      
16   16          1190197   32       Manchester United     7.265000      
17   17          1190197   14       Leicester             6.681429      
18   18          1190550   162      Crystal Palace        6.515385      
19   19          1190550   26       Liverpool             6.855000      
20   20          1190236   13       Arsenal               6.909231      
21   21          1190236   259      Swansea               6.494286      
22   22          1190222   14       Leicester             6.558571      
23   23          1190222   26       Liverpool             7.141429      
24   24          1190544   183      Bournemouth           5.961429      
25   25          1190544   26       Liverpool             7.593571      
26   26          1190223   167      Manchester City       7.666429      
27   27          1190223   26       Liverpool             5.996429      
28   28          1190545   96       Stoke                 7.498462      
29   29          1190545   175      West Bromwich Albion  6.507857      
30   30          1190551   31       Everton               6.244286      
31   31          1190551   167      Manchester City       6.947857      
32   32          1190237   167      Manchester City       7.622143      
33   33          1190237   162      Crystal Palace        6.051538      
34   34          1190196   26       Liverpool             6.937692      
35   35          1190196   184      Burnley               6.647857      
36   36          1190182   27       Watford               6.691429      
37   37          1190182   26       Liverpool             6.780000      
38   38          1190394   14       Leicester             7.220769      
39   39          1190394   27       Watford               6.454286      
40   40          1190380   183      Bournemouth           6.877143      
41   41          1190380   31       Everton               6.450714      
42   42          1190357   18       Southampton           6.874286      
43   43          1190357   96       Stoke                 7.009286      
44   44          1190431   184      Burnley               6.855455      
45   45          1190431   18       Southampton           6.812857      
46   46          1190425   14       Leicester             7.217857      
47   47          1190425   13       Arsenal               6.584615      
48   48          1190343   183      Bournemouth           6.810000      
49   49          1190343   96       Stoke                 6.945714      
50   50          1190419   13       Arsenal               6.268182      
51   51          1190419   167      Manchester City       7.444286      
52   52          1190369   27       Watford               6.988571      
53   53          1190369   175      West Bromwich Albion  6.698